In [9]:
import pandas as pd
import networkx as nx
import numpy as np
import folium
import pickle
from scipy import sparse

In [10]:
with open('data/processed/Graphs/20190901.pickle', 'rb') as f:
    graph_collection = pickle.load(f)

In [12]:
attr, adj = graph_collection[pd.Timestamp('2019-09-01 08:58:19')]

In [13]:
idx = [(r[0],r[1]) for _,r in attr[['leave_location_lat', 'leave_location_long']].iterrows()]
A_flatten = pd.DataFrame(adj.todense(), index = idx, columns = idx).stack().reset_index()¨
A_flatten = A_flatten[A_flatten[0] != 0 ]
A_flatten

In [20]:
# Function to add a point to the map
def plot_cars(map, latitude, longitude, col = 4):
    for lat, lon, c in zip(latitude, longitude, col):
        folium.CircleMarker(location=[lat, lon],
                                radius=2,
                                weight=5,
                                color = c).add_to(map)

# Function to add edges
def plot_edges(map, edge_df):
    for _, r in edge_df.iterrows():
        folium.PolyLine([r['level_0'],r['level_1']],
                    color='black',
                    weight=1,
                    opacity=r[0]/2).add_to(map)

# Initialize map
m = folium.Map(location=[55.679, 12.568337], zoom_start=12, prefer_canvas=True, width=1950,height=1400)

# Add points
plot_cars(m, attr['leave_location_lat'], attr['leave_location_long'], attr.replace({"engine": {'I3': 'Red', 'COOPER': 'Blue', '118I': 'Green', 'X1': 'Grey'}})['engine'])

plot_edges(m, A_flatten)

# Show map
m